In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from matplotlib.animation import FuncAnimation
import seaborn as sns
from scipy import stats

In [ ]:
gacha_data = pd.read_csv("gacha.csv")

In [ ]:
def convert_to_int(val):
    try:
        return int(val)
    except (ValueError, TypeError):
        return None
def parse_probability(prob_str):
    """ Parse a probability string (e.g., '2.50%') and return the numerical probability. """
    if pd.isna(prob_str):
        return 0
    return float(prob_str.strip('%')) / 100

def simulate_summons_with_probability_tracking(game_name, num_rolls, base_ssr_rate, pity_threshold, pity_increment):
    base_ssr_rate = parse_probability(base_ssr_rate)
    pity_increment = parse_probability(pity_increment)  # Ensure pity_increment is a float

    probabilities = []
    current_pity = 0

    for roll in range(num_rolls):
        if pity_threshold and roll >= pity_threshold:
            current_pity += pity_increment
        adjusted_ssr_rate = min(base_ssr_rate + current_pity, 1)
        probabilities.append(adjusted_ssr_rate)

        # Simulate the roll
        if np.random.random() < adjusted_ssr_rate:
            current_pity = 0  # Reset pity increment after an SSR is summoned
        # If SSR is not summoned, pity increments in the next iteration

    return probabilities

In [ ]:
# Example setup for animation (using hypothetical game data)
num_rolls = 300
probabilities = simulate_summons_with_probability_tracking("Example Game", num_rolls, "2%", 50, "2%")

fig, ax = plt.subplots(figsize=(10, 6)) 
line, = ax.plot([], [], lw=2)
ax.set_xlim(0, num_rolls)
ax.set_ylim(0, max(probabilities))
ax.set_xlabel('Number of Rolls')
ax.set_ylabel('Probability of SSR')

def init():
    line.set_data([], [])
    return line,

def update(frame):
    line.set_data(range(frame), probabilities[:frame])
    return line,

ani = FuncAnimation(fig, update, frames=np.arange(1, num_rolls + 1), init_func=init, blit=True)

from IPython.display import HTML
HTML(ani.to_jshtml())
ani.save('high_res_animation.gif', writer='ffmpeg', dpi=150) 

In [ ]:
# Parameters for Honkai Star Rail
num_rolls = 300  # Adjust as needed
honkai_data = gacha_data[gacha_data['Unnamed: 0'] == 'Honkai Star Rail'].iloc[0]
base_ssr_rate = parse_probability(honkai_data['Base SSR rate'])
pity_threshold = convert_to_int(honkai_data['Pity after X rolls'])
pity_increment = parse_probability(honkai_data['Pity increment (per roll)'])  

fig, ax = plt.subplots(figsize=(10, 6)) 
ax.set_xlim(0, num_rolls)
ax.set_ylim(0, 1)
ax.set_xlabel('Roll Number')
ax.set_ylabel('Result (1 for SSR, 0 for non-SSR)')
ax.set_title('Honkai Star Rail Summoning Simulation')
points, = ax.plot([], [], 'o', color='blue')
ssr_counter = ax.text(0.85, 0.95, '', transform=ax.transAxes)

def init():
    global current_pity, ssr_count
    current_pity = 0  # Reset the current pity to 0
    ssr_count = 0     # Reset the SSR count to 0
    points.set_data([], [])
    ssr_counter.set_text('SSRs: 0')
    return points, ssr_counter

def simulate_roll(base_ssr_rate, current_pity):
    adjusted_ssr_rate = min(base_ssr_rate + current_pity, 1)
    return np.random.random() < adjusted_ssr_rate

def update(frame):
    global current_pity, ssr_count
    is_ssr = simulate_roll(base_ssr_rate, current_pity)
    xdata, ydata = points.get_data()
    xdata.append(frame)
    ydata.append(int(is_ssr))
    points.set_data(xdata, ydata)

    if is_ssr:
        points.set_color('red')
        ssr_count += 1
        current_pity = 0
    else:
        current_pity += pity_increment if frame >= pity_threshold else 0
    
    ssr_counter.set_text(f'SSRs: {ssr_count}')
    return points, ssr_counter

current_pity = 0
ssr_count = 0

ani = FuncAnimation(fig, update, frames=num_rolls, init_func=init, blit=True)

HTML(ani.to_jshtml())
ani.save('gacha_summon_ani.gif', writer='ffmpeg', dpi=150) 